In [1]:
import xml.etree.ElementTree as ET
import pandas as pd
import numpy as np
import geopandas as gpd
import folium

In [2]:
# Path to the CityGML file
file_path = "/Users/maltegenschow/Documents/Uni/SoSe23/Data Science Project/data/3D_Structure/692_5336.gml"

# Parse the XML file
tree = ET.parse(file_path)
root = tree.getroot()

In [3]:
def print_element(element, indent=""):
    # Print element tag and attributes
    print(f"{indent}Tag: {element.tag}")
    for attribute, value in element.attrib.items():
        print(f"{indent}Attribute: {attribute} = {value}")
    
    # Print element text content, if available
    if element.text and element.text.strip():
        print(f"{indent}Text: {element.text.strip()}")

    # Recursively print child elements
    for child in element:
        print_element(child, indent + "  ")
#print_element(root)

In [4]:
import xml.etree.ElementTree as ET

def extract_fields(file_path):
    # Parse XML with ElementTree
    tree = ET.parse(file_path)
    root = tree.getroot()

    namespace = {'bldg': 'http://www.opengis.net/citygml/building/1.0',
                 'gen': 'http://www.opengis.net/citygml/generics/1.0',
                 'gml': 'http://www.opengis.net/gml'}

    buildings = []
    for building_elem in root.findall('.//bldg:Building', namespace):
        building = {}

        # ID of the building
        building['id'] = building_elem.get('{http://www.opengis.net/gml}id')
        # Elevation of the ground elements
        for attr_elem in building_elem.findall('.//gen:stringAttribute[@name="HoeheGrund"]/gen:value', namespace):
            building['HoeheGrund'] = float(attr_elem.text)
        # Elevation of the roof element
        for attr_elem in building_elem.findall('.//gen:stringAttribute[@name="HoeheDach"]/gen:value', namespace):
            building['HoeheDach'] = float(attr_elem.text)
        # Measured height of the building
        measuredHeight = building_elem.find('.//bldg:measuredHeight', namespace)
        if measuredHeight is not None:
            building['measuredHeight'] = float(measuredHeight.text)
        # Roof type
        roofType = building_elem.find('.//bldg:roofType', namespace)
        if roofType is not None:
            building['roofType'] = int(roofType.text)
        # Initialize lists for RoofSurface_PosList and Dachneigung
        building['RoofSurface_PosList'] = []
        building['Dachneigung'] = []
        
        for roof_elem in building_elem.findall('.//bldg:RoofSurface', namespace):
            poslist = roof_elem.find('.//gml:posList', namespace)
            if poslist is not None:
                # Append poslist text to the list
                building['RoofSurface_PosList'].append(poslist.text)

            dachneigung = roof_elem.find('.//gen:stringAttribute[@name="Dachneigung"]/gen:value', namespace)
            if dachneigung is not None:
                # Append Dachneigung text to the list
                building['Dachneigung'].append(dachneigung.text)
           
        # ground shape
        for ground_elem in building_elem.findall('.//bldg:GroundSurface', namespace):
            poslist = ground_elem.find('.//gml:posList', namespace)
            if poslist is not None:
                building['GroundSurface_PosList'] = poslist.text

        buildings.append(building)
    
    return buildings

# Use the function
file_path = "/Users/maltegenschow/Documents/Uni/SoSe23/Data Science Project/data/3D_Structure/692_5336.gml"
data = extract_fields(file_path)

#for building in data:
#    print(building)


In [5]:
df = pd.DataFrame(data)
df

id  HoeheGrund  HoeheDach  measuredHeight  roofType  \
0     DEBY_LOD2_5055095     508.426    511.800           3.374      1000   
1     DEBY_LOD2_5008284     509.650    512.066           2.416      1000   
2     DEBY_LOD2_5008024     507.580    516.580           9.000      3100   
3     DEBY_LOD2_5008772     508.490    536.820          28.330      3100   
4     DEBY_LOD2_5007891     511.130    534.720          23.590      3100   
...                 ...         ...        ...             ...       ...   
2940  DEBY_LOD2_5055360     504.560    518.458          13.898      3100   
2941  DEBY_LOD2_5054478     506.600    518.850          12.250      3200   
2942  DEBY_LOD2_5009835     508.900    516.520           7.620      1000   
2943  DEBY_LOD2_5007643     506.400    516.040           9.640      3200   
2944  DEBY_LOD2_5008752     507.968    513.634           5.666      1000   

                                    RoofSurface_PosList  \
0     [693102.39 5336225.17 511.8 693106.1 5336230.3...   
1     [692462.838 5337028.016 512.066 692459.09 5337...   
2     [692387.669 5337162.106 513.117 692383.32 5337...   
3     [692552.561 5337563.464 532.703 692552.753 533...   
4     [692026.267 5337021.799 531.552 692048.185 533...   
...                                                 ...   
2940  [693769.31 5337324.68 515.075 693766.025 53373...   
2941  [693514.786 5336362.582 516.45 693525.833 5336...   
2942  [692005.948 5337779.873 516.52 692009.197 5337...   
2943  [692737.922 5336656.343 516.04 692735.394 5336...   
2944  [692522.157 5337672.732 511.394 692527.682 533...   

                                            Dachneigung  \
0                                              [90.000]   
1                                              [90.000]   
2                              [90.000, 44.218, 44.218]   
3     [53.625, 44.603, 33.725, 33.296, 33.909, 33.90...   
4                                      [63.154, 48.668]   
...                                                 ...   
2940                                   [63.406, 63.409]   
2941           [67.786, 65.366, 67.786, 65.366, 67.802]   
2942                                   [90.000, 90.000]   
2943  [52.280, 62.393, 62.399, 62.203, 63.700, 62.38...   
2944                                           [64.423]   

                                  GroundSurface_PosList  
0     693100.98 5336226.18 508.43 693104.69 5336231....  
1     692462.318 5337024.913 509.65 692458.57 533702...  
2     692386.24 5337154.24 507.58 692383.087 5337156...  
3     692557.84 5337561.787 508.49 692553.027 533756...  
4     692023.945 5337028.001 511.13 692023.767 53370...  
...                                                 ...  
2940  693777.662 5337312.245 504.56 693766.025 53373...  
2941  693528.02 5336359.443 506.6 693525.931 5336355...  
2942  692005.024 5337786.661 508.9 692006.392 533778...  
2943  692750.703 5336648.959 506.4 692750.008 533664...  
2944  692521.326 5337672.98 507.968 692523.001 53376...  

[2945 rows x 8 columns]

In [6]:
from shapely.geometry import Polygon, MultiPolygon

def convert_3d_coordinates_to_polygons(coordinates_list):
    polygons = []
    for coordinates in coordinates_list:
        # Split the string by whitespace and remove any leading/trailing whitespace
        coord_list = [c.strip() for c in coordinates.split()]

        # Extract only the x and y coordinates, ignoring the z coordinate
        xy_coords = [(float(coord_list[i]), float(coord_list[i+1])) for i in range(0, len(coord_list), 3)]

        # Create a shapely Polygon object from the xy coordinates
        polygon = Polygon(xy_coords)
        polygons.append(polygon)

    return MultiPolygon(polygons)

In [7]:
df['geometry'] = df['RoofSurface_PosList'].apply(convert_3d_coordinates_to_polygons)
gdf = gpd.GeoDataFrame(df, geometry='geometry')
gdf.set_crs(epsg=25832, inplace=True)

gdf['geometry_4326'] = gdf['geometry'].to_crs("EPSG:4326")
# Get mask for flat and gable roofs
gdf['Dachneigung'] = gdf['Dachneigung'].apply(lambda x: [float(value) for value in x])
gable_mask = gdf['Dachneigung'].apply(lambda x: any(round(value,2) != 90.0 for value in x))

In [8]:
flat_sytle = {"fillColor": "#ff0000", 'color':'#ff0000', 'weight':0, 'fillOpacity':0.9}
gable_sytle = {"fillColor": "#0000ff", 'color':'#0000ff', 'weight':0, 'fillOpacity':0.9}


m = folium.Map(location=[gdf.geometry_4326[0].centroid.y, gdf.geometry_4326[0].centroid.x], zoom_start=18)
tile = folium.TileLayer(
        tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
        attr = 'Esri', name = 'Esri Satellite', overlay = False, control = True).add_to(m)
# add flat roofs
folium.GeoJson(gdf[~gable_mask].geometry_4326, name = 'Flat roofs', style_function=lambda x: flat_sytle).add_to(m)
# add gable roofs
folium.GeoJson(gdf[gable_mask].geometry_4326, name = 'Gable roofs', style_function=lambda x: gable_sytle).add_to(m)
folium.LayerControl().add_to(m)
m 